# Homework 1 - Mike Atwell
####Rockhurst University
####BIA6304
####2018 Fall Term 1

##Preparation

###Package imports

First we'll import all of the packages we'll need.

In [1]:
import pandas as pd   
from bs4 import BeautifulSoup
import requests
import time
import re
import numpy as np
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
import math

pd.set_option('display.max_colwidth', 150) #important for getting all the text

###Definitions

Now we'll set definitions that can be used later.

In [2]:
def remove_html_tags(text):
    """Remove html tags from a string"""
    import re
    clean = re.compile('<.*?>')
    return re.sub(clean, '', text)

##Task 1 

Task 1 is to "create a data frame containing text scraped from a website similar to headlines example done in class.  The source can be any website that contains text you may find interesting."  

We will use the Department of Defense news page here: https://dod.defense.gov/News/.  The webpage has 10 headlines displayed at any one time, so if we want more than 10 to work with, we'll have to extract from multiple pages; the code below does so using a loop.  In this case, I looped the first 50 pages; over 800 are available from the website.

Since one aspect of the business question involves looking for country names and other words associated with security cooperation, we'll keep a lookout for those.

In [3]:
base_url = 'https://dod.defense.gov/News/Archive/?Page=' #this url is the same for the start of each page
Headline_agg = [] 
Location_agg = []
Story_Date_agg = []

for i in range(0,50):  #The range determines which page numbers are scraped
    url = f'{base_url}{i}' #appends the number of this iteration of the loop to the base url
    page = requests.get(url) 
    soup = BeautifulSoup(page.text,"html5lib")
    Headline = soup.find_all('p',{'class':'title'})  #gets first desired element: headline
    Location = soup.find_all('span',{'class':'dateline'}) #gets second desired element: location
    Story_Date = soup.find_all('p',{'class':'date'}) #gets third desired element: story date
    Headline_agg.append(Headline) #takes the headline info and adds to previous iterations of the loop
    Location_agg.append(Location) #takes the location info and adds to previous iterations of the loop
    Story_Date_agg.append(Story_Date) #takes the story date info and adds to previous iterations of the loop

We've extracted the data we want from the webpage.  Now let's format to make it useable.

In [4]:
#Formats headlines

Headline_str = str(Headline_agg) #converts to string
Headline_str = Headline_str[2:-2] #removes uneeded brackets at the beginning and end
Headline_str = remove_html_tags(Headline_str) #removes unneeded html tags
Headline_str = (re.sub(',', '',Headline_str)) #next two lines remove unneeded characters
Headline_str = (re.sub('  +', '',Headline_str)) 
Headline_str = Headline_str.replace(' ','_') #substitutes spaces within headlines for _ so they won't be split up on the next line of code
Headline_str = Headline_str.split() #splits the string so that each headline is a different data element
#print(Headline_str)    #Troubleshooting tool

In [5]:
#Formats locations

Location_str = str(Location_agg) #converts to string
Location_str = Location_str.replace('—','') #removes unneeded dash in location name
Location_str = remove_html_tags(Location_str) #removes unneeded html tags
Location_str = Location_str[2:-2] #removes uneeded brackets at the beginning and end
Location_str = (re.sub(',', '',Location_str)) #next two lines remove unneeded characters
Location_str = (re.sub('  +', '',Location_str))
Location_str = Location_str.replace(' ','_') #substitutes spaces within headlines for _ so they won't be split up on the next line of code
Location_str = Location_str.split() #splits the string so that each headline is a different data element
#print(Location_str)    #Troubleshooting tool

In [6]:
#Formats story date

Story_Date_str = str(Story_Date_agg) #converts to string
Story_Date_str = remove_html_tags(Story_Date_str) #removes unneeded html tags
Story_Date_str = Story_Date_str[2:-2] #removes uneeded brackets at the beginning and end
Story_Date_str = (re.sub(',', '',Story_Date_str)) #next two lines remove unneeded characters
Story_Date_str = (re.sub('  +', '',Story_Date_str))
Story_Date_str = Story_Date_str.replace(' ','_') #substitutes spaces within headlines for _ so they won't be split up on the next line of code
Story_Date_str = Story_Date_str.replace('.','') #removes unneeded character
Story_Date_str = Story_Date_str.split() #splits the string so that each headline is a different data element
#print(Story_Date_str)    #Troubleshooting tool

Now the data is ready to be put in a dataframe.  The formatting is mostly complete, but there's a few more steps to be done. 

In [7]:
headline_data = {'Headline':Headline_str,'Location':Location_str,'Story Date':Story_Date_str}  #assigns column names
headlinedf = pd.DataFrame(headline_data) #creates dataframe
headlinedf = headlinedf.replace({'_': ' '}, regex=True) #substitutes the _ that we added earlier for a space now that the data is split
headlinedf['Access Date'] = (time.strftime("%b %d %Y")) #adds a column date for when the data was scraped
headlinedf = headlinedf.drop(headlinedf[headlinedf.Headline == '] ['].index)  #since multiple pages were scraped, this drops unecessary rows of brackets between them
headlinedf = headlinedf.reset_index(drop=True) #renumbers rows since some were dropped in the last line
pd.set_option('display.max_rows', 10) #since the dataframe is potentially very long, this restricts output to a managable length
headlinedf #shows the head and tail of the dataframe

Headline  \
0                              Dunford Arrives for Consults in Athens Readies for Indian 2+2    
1                              Coalition Strikes Continue Against ISIS Targets in Iraq Syria    
2                                        Miller Takes Over NATO U.S. Commands in Afghanistan    
3                                  McCain’s Life Celebrated at Washington National Cathedral    
4    Mattis State Department Officials Meet With Middle East Representatives at the Pentagon    
..                                                                                        ...   
495                    Military Spouse of the Year Lauded for Devotion to Gold Star Families    
496                        Balikatan 2018: U.S. Philippine Forces Share Ideas Best Practices    
497                                        Navy Volleyball Players Save Two Lives in Florida    
498                   Face of Defense: Air Force NCO Resumes Career After Tumor Hearing Loss    
499                                      Coalition Strikes Hit ISIS Terrorists in Syria Iraq    

                        Location   Story Date  Access Date  
0                 ATHENS Greece   Sept 3 2018  Sep 03 2018  
1                SOUTHWEST ASIA   Sept 3 2018  Sep 03 2018  
2                    WASHINGTON   Sept 2 2018  Sep 03 2018  
3                    WASHINGTON   Sept 1 2018  Sep 03 2018  
4                    WASHINGTON   Aug 31 2018  Sep 03 2018  
..                           ...          ...          ...  
495                  WASHINGTON   May 11 2018  Sep 03 2018  
496  CLARK AIR BASE Philippines   May 11 2018  Sep 03 2018  
497         HURLBURT FIELD Fla.   May 11 2018  Sep 03 2018  
498              FORT MEADE Md.   May 11 2018  Sep 03 2018  
499              SOUTHWEST ASIA   May 11 2018  Sep 03 2018  

[500 rows x 4 columns]

We now have a dataframe with the desired info.

##Task 2

Task 2 is "using the data from Task 1, instantiate a count vectorizer to create a bag of words. Use the default to convert to lower case.  Generate a vector space model.  Try various combinations of vectorizer settings."

We'll start by defining the method for the bag of words.  Each use of the count vectorizer below will use cv and then a number in sequence, i.e. cv1, cv2, cv3, etc.

###Getting a Bag of Words

In [8]:
textStr = headlinedf['Headline'] #creates a generic name for the headline text; useful for reusing the code for other projects 

cv1 = CountVectorizer(binary=True) #this will state only if a word appears in a sentence or not; therefore it doesn't matter if the word is used more than once in a headline

cv1_chat = cv1.fit_transform(textStr) #transforms text

print(type(cv1_chat))
print(cv1_chat.shape)

<class 'scipy.sparse.csr.csr_matrix'>
(500, 1537)


We see 1,537 unique words appeared across all 500 headlines.  Now we can list all of the words used in the headlines we selected to get the bag of words. 

In [9]:
print(cv1.get_feature_names())

['100', '101st', '11', '12000', '14th', '17', '18', '18s', '1b', '20', '200', '2002', '201', '2018', '2019', '205th', '21st', '24th', '360', '40', '43', '50', '52', '60', '69th', '717', '74th', '7b', '7th', '82nd', '983', 'abandoning', 'aboard', 'about', 'above', 'abuse', 'academy', 'accept', 'accord', 'accounting', 'achieve', 'achievement', 'achieves', 'act', 'actions', 'active', 'activity', 'adapt', 'adaptive', 'address', 'addresses', 'adds', 'advance', 'advantage', 'adversity', 'advisor', 'affairs', 'affects', 'afghan', 'afghanistan', 'afloat', 'africa', 'african', 'after', 'against', 'agencies', 'agency', 'agile', 'agree', 'ahead', 'ai', 'aid', 'aids', 'aim', 'aiming', 'aims', 'air', 'airborne', 'aircraft', 'aires', 'airlift', 'airman', 'airmen', 'alamo', 'alliance', 'alliances', 'allies', 'allowed', 'america', 'american', 'among', 'amputees', 'and', 'anniversary', 'announces', 'annual', 'another', 'app', 'appointment', 'approaches', 'approve', 'aquarium', 'area', 'argentina', 'arg

The bag of words isn't in a format yet to prove useful.  Let's put it in a dataframe.

In [10]:
pd.DataFrame(cv1_chat.toarray(),columns = cv1.get_feature_names())

100  101st  11  12000  14th  17  18  18s  1b  20  ...   wounds  wwii  \
0      0      0   0      0     0   0   0    0   0   0  ...        0     0   
1      0      0   0      0     0   0   0    0   0   0  ...        0     0   
2      0      0   0      0     0   0   0    0   0   0  ...        0     0   
3      0      0   0      0     0   0   0    0   0   0  ...        0     0   
4      0      0   0      0     0   0   0    0   0   0  ...        0     0   
..   ...    ...  ..    ...   ...  ..  ..  ...  ..  ..  ...      ...   ...   
495    0      0   0      0     0   0   0    0   0   0  ...        0     0   
496    0      0   0      0     0   0   0    0   0   0  ...        0     0   
497    0      0   0      0     0   0   0    0   0   0  ...        0     0   
498    0      0   0      0     0   0   0    0   0   0  ...        0     0   
499    0      0   0      0     0   0   0    0   0   0  ...        0     0   

     year  years  yemen  york  young  youth  zion  zone  
0       0      0      0     0      0      0     0     0  
1       0      0      0     0      0      0     0     0  
2       0      0      0     0      0      0     0     0  
3       0      0      0     0      0      0     0     0  
4       0      0      0     0      0      0     0     0  
..    ...    ...    ...   ...    ...    ...   ...   ...  
495     1      0      0     0      0      0     0     0  
496     0      0      0     0      0      0     0     0  
497     0      0      0     0      0      0     0     0  
498     0      0      0     0      0      0     0     0  
499     0      0      0     0      0      0     0     0  

[500 rows x 1537 columns]

This is a little better, but still too large and sparse to really make use of.  Let's try some operations to see only some of the words at a time.   

###Word Counts

We'll start with seeing only those words that are most used, the top 20.

In [11]:
cv2 = CountVectorizer(binary=True, max_features=20) #define the transformation
cv2_chat = cv2.fit_transform(textStr) #apply the transformation
pd.set_option('display.max_rows', 20)

names = cv2.get_feature_names()   #create list of feature names

count = np.sum(cv2_chat.toarray(), axis = 0) # convert list to array to add up feature counts 
count2 = count.tolist()  # convert numpy array to list

count_df = pd.DataFrame(count2, index = names, columns = ['count']) # create a dataframe from the list
count_df = count_df.sort_values(by = ['count'], ascending=False) # sorts the count in descending order
print(count_df)

           count
of           128
in           116
defense      103
to            93
face          79
for           63
mattis        55
dod           42
at            40
isis          38
force         38
with          37
air           36
guard         36
army          32
exercise      31
says          31
coalition     28
military      26
iraq          24


We see that several of the words are common in English such as 'to', 'with', and 'of', and these have little information content.  Let's try filtering out these common words, using the English stop words option. 

In [12]:
cv3 = CountVectorizer(binary=True, stop_words='english', max_features=20) #define the transformation
cv3_chat = cv3.fit_transform(textStr) #apply the transformation
pd.set_option('display.max_rows', 20)

names = cv3.get_feature_names()   #create list of feature names

count = np.sum(cv3_chat.toarray(), axis = 0) # convert list to array to add up feature counts 
count2 = count.tolist()  # convert numpy array to list

count_df = pd.DataFrame(count2, index = names, columns = ['count']) # create a dataframe from the list
count_df = count_df.sort_values(by = ['count'], ascending=False) # sorts the count in descending order
print(count_df)

           count
defense      103
face          79
mattis        55
dod           42
isis          38
force         38
guard         36
air           36
army          32
exercise      31
says          31
coalition     28
military      26
iraq          24
service       24
syria         24
support       22
new           19
security      18
soldier       18


Now that the common English words have been eliminated, we see several words that come as no surprise in a Defense Department news site such as 'army', 'military', 'soldier', and the Defense Secretary's name (Mattis).  'Face' initially came as a surprise, but looking at the headlines, the Department routinely runs a series called 'Face of Defense', which highlights an individual servicemember's story.

We find that 'Iraq' and 'Syria' are amongst the top 20 results, no surprise as these are two 'hotspots' with current military involvement.  Now let's try all unique words (appearing only in one headline) to see if we can extract anything useful.

In [13]:
cv4 = CountVectorizer(binary=True, stop_words='english', max_df=1) #define the transformation
cv4_chat = cv4.fit_transform(textStr) #apply the transformation
pd.set_option('display.max_rows', 10)

names = cv4.get_feature_names()   #create list of feature names

count = np.sum(cv4_chat.toarray(), axis = 0) # convert list to array to add up feature counts 
count2 = count.tolist()  # convert numpy array to list

count_df = pd.DataFrame(count2, index = names, columns = ['count']) # create a dataframe from the list
print(count_df)

         count
100          1
101st        1
12000        1
14th         1
17           1
...        ...
wounded      1
wounds       1
young        1
youth        1
zion         1

[914 rows x 1 columns]


With over 900 unique words, it's going to be hard to extract meaningful information from them.  Let's try using the min and max document frequency parameters to get words that are just below the top 20 results mentione above. 

In [14]:
cv5 = CountVectorizer(binary=True, stop_words='english', min_df=12, max_df=17) #define the transformation
cv5_chat = cv5.fit_transform(textStr) #apply the transformation
pd.set_option('display.max_rows', 20)

names = cv5.get_feature_names()   #create list of feature names

count = np.sum(cv5_chat.toarray(), axis = 0) # convert list to array to add up feature counts 
count2 = count.tolist()  # convert numpy array to list

count_df = pd.DataFrame(count2, index = names, columns = ['count']) # create a dataframe from the list
count_df = count_df.sort_values(by = ['count'], ascending=False) # sorts the count in descending order
print(count_df)

             count
nato            17
navy            17
airman          16
strikes         16
pacific         16
afghanistan     15
training        15
warrior         15
games           14
members         13
national        13
forces          13
soldiers        13
marine          12
official        12
officials       12
continue        12
targets         12
commander       12
2018            12


We find 'Afghanistan' and 'Pacific' are in the next tier just below 'Iraq' and 'Syria', a possible indication of their relative importance to Defense Department officials, and 'NATO' is present as well.  The other terms come as no surprise. 

Let's try using an n-gram to see the result from 1 to 2.

###N-Grams

In [15]:
pd.set_option('display.max_columns', None) #ensures we'll see whole dataframe
cv6 = CountVectorizer(binary=False, stop_words = 'english', ngram_range = (1,2)) #define the transformation
cv6_chat = cv6.fit_transform(textStr) #apply the transformation
pd.set_option('display.max_rows', 10) #keeps output to managable length
pd.DataFrame(cv6_chat.toarray(),columns = cv6.get_feature_names())

100  100 years  101st  101st resolute  11  11 gi  11 isis  12000  \
0      0          0      0               0   0      0        0      0   
1      0          0      0               0   0      0        0      0   
2      0          0      0               0   0      0        0      0   
3      0          0      0               0   0      0        0      0   
4      0          0      0               0   0      0        0      0   
..   ...        ...    ...             ...  ..    ...      ...    ...   
495    0          0      0               0   0      0        0      0   
496    0          0      0               0   0      0        0      0   
497    0          0      0               0   0      0        0      0   
498    0          0      0               0   0      0        0      0   
499    0          0      0               0   0      0        0      0   

     12000 migrants  14th  14th integrated  17  17 transport  18  18 exercise  \
0                 0     0                0   0             0   0            0   
1                 0     0                0   0             0   0            0   
2                 0     0                0   0             0   0            0   
3                 0     0                0   0             0   0            0   
4                 0     0                0   0             0   0            0   
..              ...   ...              ...  ..           ...  ..          ...   
495               0     0                0   0             0   0            0   
496               0     0                0   0             0   0            0   
497               0     0                0   0             0   0            0   
498               0     0                0   0             0   0            0   
499               0     0                0   0             0   0            0   

     18 participants  18 tests  18s  18s naval  1b  1b lancer  20  20 years  \
0                  0         0    0          0   0          0   0         0   
1                  0         0    0          0   0          0   0         0   
2                  0         0    0          0   0          0   0         0   
3                  0         0    0          0   0          0   0         0   
4                  0         0    0          0   0          0   0         0   
..               ...       ...  ...        ...  ..        ...  ..       ...   
495                0         0    0          0   0          0   0         0   
496                0         0    0          0   0          0   0         0   
497                0         0    0          0   0          0   0         0   
498                0         0    0          0   0          0   0         0   
499                0         0    0          0   0          0   0         0   

     200  200 miles  200 million  2002  201  201 sharpens  2018  \
0      0          0            0     0    0             0     0   
1      0          0            0     0    0             0     0   
2      0          0            0     0    0             0     0   
3      0          0            0     0    0             0     0   
4      0          0            0     0    0             0     0   
..   ...        ...          ...   ...  ...           ...   ...   
495    0          0            0     0    0             0     0   
496    0          0            0     0    0             0     1   
497    0          0            0     0    0             0     0   
498    0          0            0     0    0             0     0   
499    0          0            0     0    0             0     0   

     2018 concludes  2018 dod  2018 installation  2018 kicks  2018 philippine  \
0                 0         0                  0           0                0   
1                 0         0                  0           0                0   
2                 0         0                  0           0                0   
3                 0         0                  0           0                0

Again, this is likley too large to having meaningful information, as it has 4,045 results.  We'll need to narrow it down.  Since we already have counts of individual words, let's restrict the ngram range to 2 only.

In [16]:
pd.set_option('display.max_columns', None) #ensures we'll see whole dataframe
cv7 = CountVectorizer(binary=False, stop_words = 'english', ngram_range = (2,2)) #define the transformation
cv7_chat = cv7.fit_transform(textStr) #apply the transformation
pd.set_option('display.max_rows', 10) #keeps output to managable length
pd.DataFrame(cv7_chat.toarray(),columns = cv7.get_feature_names())

100 years  101st resolute  11 gi  11 isis  12000 migrants  \
0            0               0      0        0               0   
1            0               0      0        0               0   
2            0               0      0        0               0   
3            0               0      0        0               0   
4            0               0      0        0               0   
..         ...             ...    ...      ...             ...   
495          0               0      0        0               0   
496          0               0      0        0               0   
497          0               0      0        0               0   
498          0               0      0        0               0   
499          0               0      0        0               0   

     14th integrated  17 transport  18 exercise  18 participants  18 tests  \
0                  0             0            0                0         0   
1                  0             0            0                0         0   
2                  0             0            0                0         0   
3                  0             0            0                0         0   
4                  0             0            0                0         0   
..               ...           ...          ...              ...       ...   
495                0             0            0                0         0   
496                0             0            0                0         0   
497                0             0            0                0         0   
498                0             0            0                0         0   
499                0             0            0                0         0   

     18s naval  1b lancer  20 years  200 miles  200 million  201 sharpens  \
0            0          0         0          0            0             0   
1            0          0         0          0            0             0   
2            0          0         0          0            0             0   
3            0          0         0          0            0             0   
4            0          0         0          0            0             0   
..         ...        ...       ...        ...          ...           ...   
495          0          0         0          0            0             0   
496          0          0         0          0            0             0   
497          0          0         0          0            0             0   
498          0          0         0          0            0             0   
499          0          0         0          0            0             0   

     2018 concludes  2018 dod  2018 installation  2018 kicks  2018 philippine  \
0                 0         0                  0           0                0   
1                 0         0                  0           0                0   
2                 0         0                  0           0                0   
3                 0         0                  0           0                0   
4                 0         0                  0           0                0   
..              ...       ...                ...         ...              ...   
495               0         0                  0           0                0   
496               0         0                  0           0                1   
497               0         0                  0           0                0   
498               0         0                  0           0                0   
499               0         0                  0           0                0   

     2018 vietnam  2019 defense  205th corps  21st century  24th cooperation  \
0               0             0            0             0                 0   
1               0             0            0             0                 0   
2               0             0            0             0                 0   
3               0             0            0             

This produced 2,589 results.  Let's do a count to see the most common (top 20) two-word combinations.  

In [17]:
pd.set_option('display.max_rows', 20) #keeps output to desired length
names = cv7.get_feature_names()   #create list of feature names
count = np.sum(cv7_chat.toarray(), axis = 0) # convert list to array to add up feature counts 
count2 = count.tolist()  # convert numpy array to list
count_df = pd.DataFrame(count2, index = names, columns = ['count']) # create a dataframe from the list
count_df = count_df.sort_values(by = ['count'], ascending=False) # sort results in descending order
print(count_df.head(20))

                      count
face defense             77
air force                26
warrior games            14
coalition strikes        14
defense airman           13
mattis says              11
operation roundup        10
iraq syria               10
service members          10
continue isis             9
strikes continue          9
dod warrior               9
isis targets              9
indo pacific              9
syria iraq                8
national guard            8
isis terrorists           7
isis remnants             7
defense relationship      6
coast guard               6


None of these combinations come as any surprise.  Iraq and Syria appear together, as does Indo-Pacific.  Let's try one last n-gram, with three word combinations only, and get a count.  

In [18]:
pd.set_option('display.max_columns', None) #ensures we'll see whole dataframe
cv8 = CountVectorizer(binary=False, stop_words = 'english', ngram_range = (3,3)) #define the transformation
cv8_chat = cv8.fit_transform(textStr) #apply the transformation
pd.set_option('display.max_rows', 10) #keeps output to managable length
pd.DataFrame(cv8_chat.toarray(),columns = cv8.get_feature_names())

100 years mateship  101st resolute support  11 gi benefits  \
0                     0                       0               0   
1                     0                       0               0   
2                     0                       0               0   
3                     0                       0               0   
4                     0                       0               0   
..                  ...                     ...             ...   
495                   0                       0               0   
496                   0                       0               0   
497                   0                       0               0   
498                   0                       0               0   
499                   0                       0               0   

     11 isis fighters  14th integrated defense  17 transport jet  \
0                   0                        0                 0   
1                   0                        0                 0   
2                   0                        0                 0   
3                   0                        0                 0   
4                   0                        0                 0   
..                ...                      ...               ...   
495                 0                        0                 0   
496                 0                        0                 0   
497                 0                        0                 0   
498                 0                        0                 0   
499                 0                        0                 0   

     18 exercise concludes  18 participants mull  18 tests mississippi  \
0                        0                     0                     0   
1                        0                     0                     0   
2                        0                     0                     0   
3                        0                     0                     0   
4                        0                     0                     0   
..                     ...                   ...                   ...   
495                      0                     0                     0   
496                      0                     0                     0   
497                      0                     0                     0   
498                      0                     0                     0   
499                      0                     0                     0   

     18s naval aviation  1b lancer bombers  200 miles hour  \
0                     0                  0               0   
1                     0                  0               0   
2                     0                  0               0   
3                     0                  0               0   
4                     0                  0               0   
..                  ...                ...             ...   
495                   0                  0               0   
496                   0                  0               0   
497                   0                  0               0   
498                   0                  0               0   
499                   0                  0               0   

     200 million security  201 sharpens community  2018 concludes morocco  \
0                       0                       0                       0   
1                       0                       0                       0   
2                       0                       0                       0   
3                       0                       0                       0   
4                       0                       0                       0   
..                    ...                     ...                     ...   
495                     0                       0                       0   
496                     0                       0                       0   
497                     0                       0       

This produced 2,449 results.  Let's do a count to see the most common three-word combinations.  

In [19]:
pd.set_option('display.max_rows', 20)  #keeps output to desired length
names = cv8.get_feature_names()   #create list of feature names

count = np.sum(cv8_chat.toarray(), axis = 0) # convert list to array to add up feature counts 
count2 = count.tolist()  # convert numpy array to list

count_df = pd.DataFrame(count2, index = names, columns = ['count']) # create a dataframe from the list
count_df = count_df.sort_values(by = ['count'], ascending=False)  # sort results in descending order
print(count_df.head(20))

                            count
face defense airman            13
dod warrior games               9
strikes continue isis           9
coalition strikes continue      9
continue isis targets           9
face defense navy               5
face defense army               5
face defense soldier            5
targets iraq syria              5
isis targets iraq               5
remnants iraq syria             4
targets syria iraq              4
isis targets syria              4
isis remnants iraq              4
face defense air                4
isis terrorists syria           3
strikes target isis             3
terrorists syria iraq           3
coalition strikes target        3
face defense marine             3


No real surprises here, Iraq and Syria again appear together, sometimes with ISIS in the headline as well. Now we'll move on to a TF-IDF vectorizer for additional analysis.

###TF-IDF Vectorizer

First we'll try the TF-IDF without using inverse document frequency reweighting.

In [20]:
pd.set_option('display.max_rows', 10) #keeps output to managable length
tfidf1 = TfidfVectorizer(use_idf=False, norm=None, stop_words='english') #define the transformation
tf1_chat = tfidf1.fit_transform(textStr) #apply the transformation
pd.DataFrame(tf1_chat.toarray(),columns = tfidf1.get_feature_names())

100  101st   11  12000  14th   17   18  18s   1b   20  200  2002  201  \
0    0.0    0.0  0.0    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
1    0.0    0.0  0.0    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
2    0.0    0.0  0.0    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
3    0.0    0.0  0.0    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
4    0.0    0.0  0.0    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
..   ...    ...  ...    ...   ...  ...  ...  ...  ...  ...  ...   ...  ...   
495  0.0    0.0  0.0    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
496  0.0    0.0  0.0    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
497  0.0    0.0  0.0    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
498  0.0    0.0  0.0    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
499  0.0    0.0  0.0    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   

     2018  2019  205th  21st  24th  360   40   43   50   52   60  69th  717  \
0     0.0   0.0    0.0   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
1     0.0   0.0    0.0   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
2     0.0   0.0    0.0   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
3     0.0   0.0    0.0   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
4     0.0   0.0    0.0   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
..    ...   ...    ...   ...   ...  ...  ...  ...  ...  ...  ...   ...  ...   
495   0.0   0.0    0.0   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
496   1.0   0.0    0.0   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
497   0.0   0.0    0.0   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
498   0.0   0.0    0.0   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
499   0.0   0.0    0.0   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   

     74th   7b  7th  82nd  983  abandoning  aboard  abuse  academy  accept  \
0     0.0  0.0  0.0   0.0  0.0         0.0     0.0    0.0      0.0     0.0   
1     0.0  0.0  0.0   0.0  0.0         0.0     0.0    0.0      0.0     0.0   
2     0.0  0.0  0.0   0.0  0.0         0.0     0.0    0.0      0.0     0.0   
3     0.0  0.0  0.0   0.0  0.0         0.0     0.0    0.0      0.0     0.0   
4     0.0  0.0  0.0   0.0  0.0         0.0     0.0    0.0      0.0     0.0   
..    ...  ...  ...   ...  ...         ...     ...    ...      ...     ...   
495   0.0  0.0  0.0   0.0  0.0         0.0     0.0    0.0      0.0     0.0   
496   0.0  0.0  0.0   0.0  0.0         0.0     0.0    0.0      0.0     0.0   
497   0.0  0.0  0.0   0.0  0.0         0.0     0.0    0.0      0.0     0.0   
498   0.0  0.0  0.0   0.0  0.0         0.0     0.0    0.0      0.0     0.0   
499   0.0  0.0  0.0   0.0  0.0         0.0     0.0    0.0      0.0     0.0   

     accord  accounting  achieve  achievement  achieves  act  actions  active  \
0       0.0         0.0      0.0          0.0       0.0  0.0      0.0     0.0   
1       0.0         0.0      0.0          0.0       0.0  0.0      0.0     0.0   
2       0.0         0.0      0.0          0.0       0.0  0.0      0.0     0.0   
3       0.0         0.0      0.0          0.0       0.0  0.0      0.0     0.0   
4       0.0         0.0      0.0          0.0       0.0  0.0      0.0     0.0   
..      ...         ...      ...          ...       ...  ...      ...     ...   
495     0.0         0.0      0.0          0.0       0.0  0.0      0.0     0.0   
496     0.0         0.0      0.0          0.0       0.0  0.0      0.0     0.0   
497     0.0         0.0      0.0          0.0       0.0  0.0      0.0     0.0   
498     0.0         0.0      0.0          0.0       0.0  0.0      0.0     0.0   
499     0.0         0.0      0.0          0.0       0.0  0.0      0.0     0.0   

     activity  adapt  adaptive  address  addresses  adds  advance  advantage  \
0         0.0    0.0       0.0      0.0        0.0   0.0      0.0        0.0   
1         0.0    0.0       0.0      0.0        0.

The dataframe isn't really usable in this format.  Let's see the top and bottom results.

In [21]:
pd.set_option('display.max_rows', 20) 

names = tfidf1.get_feature_names()   #create list of feature names

count = np.sum(tf1_chat.toarray(), axis = 0) # convert list to array to add up feature counts 
count2 = count.tolist()  # convert numpy array to list

count_df = pd.DataFrame(count2, index = names, columns = ['count']) # create a dataframe from the list
count_df = count_df.sort_values(by = ['count'], ascending=False) #sorts count in descending order
print(count_df)

              count
defense       104.0
face           79.0
mattis         55.0
dod            42.0
force          39.0
isis           38.0
air            38.0
guard          36.0
army           32.0
says           31.0
...             ...
counter         1.0
maintainers     1.0
maintenance     1.0
maj             1.0
major           1.0
cosmic          1.0
cornerstone     1.0
coordinators    1.0
malaysia        1.0
100             1.0

[1456 rows x 1 columns]


The count results were no different than what we saw before since we're not using inverse document frequency reweighting.  Let's try that now.

In [22]:
pd.set_option('display.max_rows', 10) 

tfidf2 = TfidfVectorizer(use_idf=True, norm=None, stop_words='english') #define the transformation
tf2_chat = tfidf2.fit_transform(textStr) #apply the transformation

pd.DataFrame(tf2_chat.toarray(),columns = tfidf2.get_feature_names())

100  101st   11  12000  14th   17   18  18s   1b   20  200  2002  201  \
0    0.0    0.0  0.0    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
1    0.0    0.0  0.0    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
2    0.0    0.0  0.0    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
3    0.0    0.0  0.0    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
4    0.0    0.0  0.0    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
..   ...    ...  ...    ...   ...  ...  ...  ...  ...  ...  ...   ...  ...   
495  0.0    0.0  0.0    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
496  0.0    0.0  0.0    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
497  0.0    0.0  0.0    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
498  0.0    0.0  0.0    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
499  0.0    0.0  0.0    0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   

         2018  2019  205th  21st  24th  360   40   43   50   52   60  69th  \
0    0.000000   0.0    0.0   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
1    0.000000   0.0    0.0   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
2    0.000000   0.0    0.0   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
3    0.000000   0.0    0.0   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
4    0.000000   0.0    0.0   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
..        ...   ...    ...   ...   ...  ...  ...  ...  ...  ...  ...   ...   
495  0.000000   0.0    0.0   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
496  4.651657   0.0    0.0   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
497  0.000000   0.0    0.0   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
498  0.000000   0.0    0.0   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   
499  0.000000   0.0    0.0   0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   

     717  74th   7b  7th  82nd  983  abandoning  aboard  abuse  academy  \
0    0.0   0.0  0.0  0.0   0.0  0.0         0.0     0.0    0.0      0.0   
1    0.0   0.0  0.0  0.0   0.0  0.0         0.0     0.0    0.0      0.0   
2    0.0   0.0  0.0  0.0   0.0  0.0         0.0     0.0    0.0      0.0   
3    0.0   0.0  0.0  0.0   0.0  0.0         0.0     0.0    0.0      0.0   
4    0.0   0.0  0.0  0.0   0.0  0.0         0.0     0.0    0.0      0.0   
..   ...   ...  ...  ...   ...  ...         ...     ...    ...      ...   
495  0.0   0.0  0.0  0.0   0.0  0.0         0.0     0.0    0.0      0.0   
496  0.0   0.0  0.0  0.0   0.0  0.0         0.0     0.0    0.0      0.0   
497  0.0   0.0  0.0  0.0   0.0  0.0         0.0     0.0    0.0      0.0   
498  0.0   0.0  0.0  0.0   0.0  0.0         0.0     0.0    0.0      0.0   
499  0.0   0.0  0.0  0.0   0.0  0.0         0.0     0.0    0.0      0.0   

     accept  accord  accounting  achieve  achievement  achieves  act  actions  \
0       0.0     0.0         0.0      0.0          0.0       0.0  0.0      0.0   
1       0.0     0.0         0.0      0.0          0.0       0.0  0.0      0.0   
2       0.0     0.0         0.0      0.0          0.0       0.0  0.0      0.0   
3       0.0     0.0         0.0      0.0          0.0       0.0  0.0      0.0   
4       0.0     0.0         0.0      0.0          0.0       0.0  0.0      0.0   
..      ...     ...         ...      ...          ...       ...  ...      ...   
495     0.0     0.0         0.0      0.0          0.0       0.0  0.0      0.0   
496     0.0     0.0         0.0      0.0          0.0       0.0  0.0      0.0   
497     0.0     0.0         0.0      0.0          0.0       0.0  0.0      0.0   
498     0.0     0.0         0.0      0.0          0.0       0.0  0.0      0.0   
499     0.0     0.0         0.0      0.0          0.0       0.0  0.0      0.0   

     active  activity  adapt  adaptive  address  addresses  adds  advance  \
0       0.0       0.0    0.0       0.0      0.0        0.0   0.0      0.0   
1       0.0       0.0    0.0       0.0      0.0        0.0   0.0      0.0   
2       0.0       0.0    0

We have the dataframe using inverse document frequency reweighting, but it isn't yet useful.  Let's see the top and bottom results.

In [23]:
pd.set_option('display.max_rows', 20) #sets output to desired length

names = tfidf2.get_feature_names()   #create list of feature names

count = np.sum(tf2_chat.toarray(), axis = 0) # convert list to array to add up feature counts 
count2 = count.tolist()  # convert numpy array to list

count_df = pd.DataFrame(count2, index = names, columns = ['count']) # create a dataframe from the list
count_df = count_df.sort_values(by = ['count'], ascending=False) #sorts results in descending order
print(count_df)

                   count
defense       267.510381
face          223.931778
mattis        175.518993
dod           145.127051
force         138.568734
air           137.016151
isis          135.015689
guard         129.804775
army          119.043153
says          116.276976
...                  ...
counter         6.523459
maintainers     6.523459
maintenance     6.523459
maj             6.523459
major           6.523459
cosmic          6.523459
cornerstone     6.523459
coordinators    6.523459
malaysia        6.523459
100             6.523459

[1456 rows x 1 columns]


The count numbers are higher, but the order is no different.  That said, the ratio of the differences between two words has changed.  For instance, previously defense:army had a ratio of 104:32, or about 3.3 times higher.  Now, defense:army has a ratio of 267.5:119.0, or about 2.2 times higher.

Now let's try the average weight of each feature and see the results.

In [24]:
count = np.mean(tf2_chat.toarray(), axis = 0) # find the average weight for each feature 
count2 = count.tolist()  # convert numpy array to list
count_df = pd.DataFrame(count2, index = names, columns = ['count']) # create a dataframe from the list
count_df = count_df.sort_values(by = ['count'], ascending=False) #sorts 
print(count_df)

                 count
defense       0.535021
face          0.447864
mattis        0.351038
dod           0.290254
force         0.277137
air           0.274032
isis          0.270031
guard         0.259610
army          0.238086
says          0.232554
...                ...
counter       0.013047
maintainers   0.013047
maintenance   0.013047
maj           0.013047
major         0.013047
cosmic        0.013047
cornerstone   0.013047
coordinators  0.013047
malaysia      0.013047
100           0.013047

[1456 rows x 1 columns]


Average weight produced results with ratios equal to the previous example.  Now let's try the maximum weight with each column and see the result.

In [25]:
pd.set_option('display.max_rows', 20) #sets output to desired length
count = np.max(tf2_chat.toarray(), axis = 0) # find the max weight of each feature 
count2 = count.tolist()  # convert numpy array to list
count_df = pd.DataFrame(count2, index = names, columns = ['count']) # create a dataframe from the list
count_df = count_df.sort_values(by = ['count'], ascending=False) #sorts values in descending order
print(count_df)

                count
sama        13.046918
test        11.214336
enlisted    10.849693
space       10.038763
service      7.995461
air          7.211376
force        7.106089
100          6.523459
salute       6.523459
salvadoran   6.523459
...               ...
military     3.920769
coalition    3.849310
exercise     3.750870
says         3.750870
army         3.720099
guard        3.605688
isis         3.553044
dod          3.455406
mattis       3.191254
face         2.834579

[1456 rows x 1 columns]


With this option the maximum weight is shown.  Most of the previous top results wound up near the bottom.

##Applying a Country Filter
####(This is not a task assigned in the homework, but wanted to try this to see how targeted we could make the results).

Since we're mainly interested in different countries in the headlines, it makes sense to apply a filter of those words relating to different countries.  We can't just use country names as different forms of the name may be used in a headline, e.g. 'Argentina' or 'Argentine'.  I used this page: https://www.cia.gov/library/publications/the-world-factbook/fields/2110.html which has a useful list of different variations on a country's name or its people in different grammatical contexts, and put those words in a csv file.

In [26]:
pd.set_option('display.max_rows', 10) #sets output to desired length
country_list = pd.read_csv("CountryWordListLowerCase.csv", header=None) #imports csv
country_list

0
0         afghan
1    afghanistan
2        afghans
3         africa
4        african
..           ...
675    zealander
676   zealanders
677     zimbabwe
678   zimbabwean
679  zimbabweans

[680 rows x 1 columns]

Now we'll compare this list with the words in the headlines to get a count of country mentions.

In [27]:
cv9 = CountVectorizer(binary=True, stop_words='english') #define the transformation

cv9_chat = cv9.fit_transform(textStr) #apply the transformation

names = cv9.get_feature_names()   #create list of feature names

count = np.sum(cv9_chat.toarray(), axis = 0) # convert list to array to add up feature counts 
count2 = count.tolist()  # convert numpy array to list

data = {'country': names, 'count': count2} #columns for dataframe
count_df = pd.DataFrame(data=data) # create a dataframe from the list

pd.set_option('display.max_rows', 20) #sets output to desired length

set1 = set(count_df['country']) #all words in the headlines
set2 = set(country_list[0]) #all countries and country-related words 
set3 = set2 - set1  #all countries not mentioned in headlines
set4 = set2 - set3  #all countries mentioned in the headlines

count_df = count_df.loc[count_df['country'].isin(set4)] #reduces dataframe rows only to those countries in headlines 
count_df = count_df.set_index('country') #removes unneeded row numbers
count_df = count_df.sort_values(by = ['count'], ascending=False) #sorts values in descending order

count_df

count
country           
iraq            24
syria           24
afghanistan     15
korea            6
vietnam          5
guam             5
iraqi            5
korean           5
afghan           4
panama           4
...            ...
jordan           1
kenyan           1
kuwait           1
lebanon          1
lithuania        1
lithuanian       1
malaysia         1
central          1
mexico           1
italian          1

[82 rows x 1 columns]

We now have a count of what countries and country-related words were in the headlines.  While some come as no surprise (Iraq, Syria, Afghanistan, and even Korea), I did not expect some others (Vietnam, Georgia) to be mentioned so often.

##Conclusion

Initial results show there is some value added to mining these headlines for information.  We can get a sense of how important a given country or region is to the Department of Defense by how frequently it is reported on in their news headlines.  A few ways to make these results more useful:

- Improved the filter for country names so that related words such as 'Iraq' and 'Iraqi' are transformed to one country name, thus getting a more accurate count of how many headlines are relevant to a given country.
- Consider screening for other words or phrases we might be interested in (e.g. 'security cooperation' or 'advising').
- Create the ability to show change over time.
- Conduct more detailed analysis of other words that appear with the country-related words.